In [1]:
import numpy as np
import pickle as pkl
import os
from PIL import Image
from matplotlib import pyplot as plt
import matplotlib.patches as patches
from math import floor, ceil
import time

In [2]:
feature_before = np.random.rand(50,70,1024)
feature_after = np.random.rand(50,70,1024)

In [3]:
def get_max_and_concat(*args):
    size = 0
    for arg in args:
        size += arg.shape[-1]
    final = np.zeros(size)
    
    arg_size = 0

    for arg in args:
        for i in range(arg.shape[-1]):
            final[i+arg_size] = np.max(arg[:,:,i])
        arg_size += arg.shape[-1]

    return final
        

In [4]:
SESSIONS_PATH = "/home/wc-gpu/storage4tb/session_data_thesis/sessions160000_165000"
IMAGE_SIZE = (30, 20)
plot_features_and_annotations = True

In [5]:
# for session in sorted(os.listdir(SESSIONS_PATH)):
#     try:
#         a = int(session)

#         features_path = os.path.join(SESSIONS_PATH, session, "features")
#         boxes_path = os.path.join(SESSIONS_PATH, session, "boxes")
#         session_path = os.path.join(SESSIONS_PATH, session)
#         if not os.path.exists(os.path.join(features_path)) or not os.path.exists(os.path.join(boxes_path)) :
#             continue

#         for image_file in sorted(os.listdir(session_path)):
#             try:
#                 if not image_file.endswith(".jpg"):
#                     continue
#                 feature_path = os.path.join(features_path, image_file + ".feature.prod.new")
                
#                 boxe_path = os.path.join(boxes_path, image_file + ".box")
#                 features = None
#                 boxes = None
#                 with open(feature_path, "rb") as f:
#                     features = np.load(f)
#                 with open(boxe_path, "rb") as f:
#                     boxes = pkl.load(f)
                
#                 features = features[0]
#                 print ("SHAPE", features.shape)
#                 image_np = features[:,:,500]
#                 image_np *= 255.0/image_np.max()  

#                 fig,ax = plt.subplots(1, figsize=IMAGE_SIZE)

#                 ax.imshow(image_np)
#                 for label in boxes[0]:
#                     rect = patches.Rectangle(
#                         (label[1]*image_np.shape[1],label[0]*image_np.shape[0]),
#                         (label[3]-label[1])*image_np.shape[1],
#                         (label[2]-label[0])*image_np.shape[0],
#                         linewidth=5,edgecolor='r',facecolor='none')
#                     ax.add_patch(rect)

#                 for label in boxes[1]:
#                     rect = patches.Rectangle(
#                         (label[1]*image_np.shape[1],label[0]*image_np.shape[0]),
#                         (label[3]-label[1])*image_np.shape[1],
#                         (label[2]-label[0])*image_np.shape[0],
#                         linewidth=5,edgecolor='g',facecolor='none')
#                     ax.add_patch(rect)
#                 plt.show(IMAGE_SIZE)
                
                
#                 print("negatives")
#                 for label in boxes[0]:
# #                     print (
# #                         floor(label[0]*image_np.shape[0]),
# #                         ceil(label[2]*image_np.shape[0]),
# #                         floor(label[1]*image_np.shape[1]),
# #                         ceil(label[3]*image_np.shape[1]))
#                     rect = features[
#                         floor(label[0]*image_np.shape[0]):
#                         ceil(label[2]*image_np.shape[0]), 
#                         floor(label[1]*image_np.shape[1]):
#                         ceil(label[3]*image_np.shape[1])]
#                     fig,ax = plt.subplots(1)
#                     ax.imshow(rect[:,:,500])
#                     plt.show()
                    
                
                
#                 print("positives")
#                 for label in boxes[1]:
#                     rect = features[
#                         floor(label[0]*image_np.shape[0]):
#                         ceil(label[2]*image_np.shape[0]), 
#                         floor(label[1]*image_np.shape[1]):
#                         ceil(label[3]*image_np.shape[1])]
#                     fig,ax = plt.subplots(1)
#                     ax.imshow(rect[:,:,500])
#                     plt.show()
                    
                
#             except Exception as ex:
#                 print (session, ex)
#                 continue
#         break
#     except Exception as ex:
#         print (session, ex)
#         continue
    

In [6]:
X = []
Y = []

total_images = 0
sessions = os.listdir(SESSIONS_PATH)
actual_sessions = []

for session in sorted(sessions, reverse=True):
    try:
        a = int(session)
        session_path = os.path.join(SESSIONS_PATH, session)
        boxes_path = os.path.join(session_path, "boxes")
        features_path = os.path.join(session_path, "features")
        
        if os.path.exists(features_path) and os.path.exists(boxes_path):
            actual_sessions.append(session)
            images = [f for f in os.listdir(session_path) if f.endswith(".jpg")]
            total_images += len(images)
    except:
        print (session)
        continue
        
progress = 0

processed = 0
time_avg = 0

for session in sorted(actual_sessions):
    try:
        features_path = os.path.join(SESSIONS_PATH, session, "features")
        boxes_path = os.path.join(SESSIONS_PATH, session, "boxes")
        session_path = os.path.join(SESSIONS_PATH, session)
        previous_features = None
        previous_boxes = None
        for image_file in sorted(os.listdir(session_path)):
            try:
                if image_file.endswith(".jpg"):

                    t0 = time.time()

                    feature_path = os.path.join(features_path, image_file + ".feature.prod.new.better")
                    if not os.path.exists(features_path):
                        break
                    boxe_path = os.path.join(boxes_path, image_file + ".box.better")
                    features = None
                    boxes = None
                    with open(feature_path, "rb") as f:
                        features = np.load(f)[0]
                    with open(boxe_path, "rb") as f:
                        boxes = pkl.load(f)

    #                 mn = np.mean(features)
    # #                 print (mn.shape)
    #                 std = np.std(features)
    # #                 print (std.shape)

    #                 features = (features - mn)/std

                    if previous_features is not None:
                        for label in boxes[0]:
                            box_prev = previous_features[
                                floor(label[0]*previous_features.shape[0]):
                                ceil(label[2]*previous_features.shape[0]), 
                                floor(label[1]*previous_features.shape[1]):
                                ceil(label[3]*previous_features.shape[1]),:]
                            box_cur = features[
                                floor(label[0]*features.shape[0]):
                                ceil(label[2]*features.shape[0]), 
                                floor(label[1]*features.shape[1]):
                                ceil(label[3]*features.shape[1]),:]

                            max_pooled = get_max_and_concat(box_prev, previous_features, box_cur, features)
                            X.append(max_pooled)
                            Y.append(0)

                        for label in boxes[1]:
                            if(label[4] == "add"):
                                box_prev = previous_features[
                                    floor(label[0]*previous_features.shape[0]):
                                    ceil(label[2]*previous_features.shape[0]), 
                                    floor(label[1]*previous_features.shape[1]):
                                    ceil(label[3]*previous_features.shape[1]),:]
                                box_cur = features[
                                    floor(label[0]*features.shape[0]):
                                    ceil(label[2]*features.shape[0]), 
                                    floor(label[1]*features.shape[1]):
                                    ceil(label[3]*features.shape[1]),:]

                                max_pooled = get_max_and_concat(box_prev, previous_features, box_cur, features)
                                X.append(max_pooled)
                                Y.append(1)

                        for label in previous_boxes[1]:
                            if(label[4] == "remove"):
                                box_prev = previous_features[
                                    floor(label[0]*previous_features.shape[0]):
                                    ceil(label[2]*previous_features.shape[0]), 
                                    floor(label[1]*previous_features.shape[1]):
                                    ceil(label[3]*previous_features.shape[1]),:]
                                box_cur = features[
                                    floor(label[0]*features.shape[0]):
                                    ceil(label[2]*features.shape[0]), 
                                    floor(label[1]*features.shape[1]):
                                    ceil(label[3]*features.shape[1]),:]

                                max_pooled = get_max_and_concat(box_prev, previous_features, box_cur, features)
                                X.append(max_pooled)
                                Y.append(1)

                    previous_features = features
                    previous_boxes = boxes

                    total_time = time_avg * processed
                    processed += 1

                    t1 = time.time()

                    total = t1-t0
                    print ("total time", total)

                    time_avg = (total_time + total) / processed

                    print ("progress", session, "  : ", progress / total_images, progress, total_images)
                    print ("time", session, "  passed: ", time_avg*processed / 3600 ," h  expected left: ", time_avg* (total_images - progress) / 3600, " h")

                    progress += 1
                
            except Exception as ex:
                print (session, ex)
    except Exception as ex:
        print (session, ex)
    

old_ds
max_breaks.pkl
total time 0.04771828651428223
progress 117653   :  0.0 0 25325
time 117653   passed:  1.3255079587300618e-05  h  expected left:  0.3356848905483882  h
total time 0.07328605651855469
progress 117653   :  3.948667324777888e-05 1 25325
time 117653   passed:  3.361231750912137e-05  h  expected left:  0.4255991643004947  h
total time 0.06553459167480469
progress 117653   :  7.897334649555775e-05 2 25325
time 117653   passed:  5.181637075212267e-05  h  expected left:  0.4373819855186674  h
total time 0.06339645385742188
progress 117653   :  0.00011846001974333662 3 25325
time 117653   passed:  6.942649682362874e-05  h  expected left:  0.43950443814198176  h
total time 0.04967474937438965
progress 117653   :  0.0001579466929911155 4 25325
time 117653   passed:  8.322503831651476e-05  h  expected left:  0.4214682390424941  h
total time 0.056322574615478516
progress 117653   :  0.00019743336623889436 5 25325
time 117653   passed:  9.887019793192545e-05  h  expected left: 

total time 0.05147957801818848
progress 117684   :  0.0019348469891411649 49 25325
time 117684   passed:  0.0007317383421791924  h  expected left:  0.36990836673842536  h
total time 0.039261817932128906
progress 117684   :  0.0019743336623889436 50 25325
time 117684   passed:  0.0007426444027158949  h  expected left:  0.3680458289930244  h
total time 0.037251949310302734
progress 117684   :  0.0020138203356367228 51 25325
time 117684   passed:  0.0007529921664132012  h  expected left:  0.3659831541139855  h
total time 0.05183863639831543
progress 117684   :  0.0020533070088845015 52 25325
time 117684   passed:  0.0007673917876349555  h  expected left:  0.3659300499792119  h
total time 0.03937578201293945
progress 117684   :  0.0020927936821322803 53 25325
time 117684   passed:  0.000778329504860772  h  expected left:  0.3642582082748413  h
total time 0.03677678108215332
progress 117684   :  0.0021322803553800594 54 25325
time 117684   passed:  0.0007885452773835924  h  expected left:  

total time 0.24765253067016602
progress 117684   :  0.0038696939782823297 98 25325
time 117684   passed:  0.0014576447672314113  h  expected left:  0.37143438932269507  h
total time 0.04678845405578613
progress 117684   :  0.0039091806515301085 99 25325
time 117684   passed:  0.0014706415600246852  h  expected left:  0.37098403993182716  h
total time 0.04211783409118652
progress 117684   :  0.003948667324777887 100 25325
time 117684   passed:  0.0014823409583833483  h  expected left:  0.3702183235170293  h
total time 0.04285693168640137
progress 117684   :  0.003988153998025666 101 25325
time 117684   passed:  0.001494245661629571  h  expected left:  0.3695181624406303  h
total time 0.05611777305603027
progress 117684   :  0.0040276406712734455 102 25325
time 117684   passed:  0.0015098339319229127  h  expected left:  0.3697334103387536  h
total time 0.04958963394165039
progress 117684   :  0.004067127344521224 103 25325
time 117684   passed:  0.0015236088302400376  h  expected left:  

total time 0.04939603805541992
progress 117687   :  0.005844027640671274 148 25325
time 117687   passed:  0.00210034085644616  h  expected left:  0.35490121974996625  h
total time 0.05284428596496582
progress 117687   :  0.0058835143139190525 149 25325
time 117687   passed:  0.0021150198247697617  h  expected left:  0.3549849273893568  h
total time 0.040085792541503906
progress 117687   :  0.005923000987166831 150 25325
time 117687   passed:  0.0021261547671424016  h  expected left:  0.35447646531662225  h
total time 0.056974172592163086
progress 117687   :  0.00596248766041461 151 25325
time 117687   passed:  0.00214198092619578  h  expected left:  0.3547514989213985  h
total time 0.07024645805358887
progress 117687   :  0.006001974333662389 152 25325
time 117687   passed:  0.002161493831210666  h  expected left:  0.3556293085821313  h
total time 0.07920479774475098
progress 117687   :  0.0060414610069101675 153 25325
time 117687   passed:  0.002183495163917541  h  expected left:  0.3

total time 0.16311073303222656
progress 118859   :  0.007778874629812438 197 25325
time 118859   passed:  0.002847039235962762  h  expected left:  0.36131516121854684  h
total time 0.12624216079711914
progress 118859   :  0.007818361303060217 198 25325
time 118859   passed:  0.0028821065028508505  h  expected left:  0.36391301556348404  h
total time 0.05266118049621582
progress 118859   :  0.007857847976307996 199 25325
time 118859   passed:  0.002896734608544244  h  expected left:  0.36391676887141333  h
total time 0.05241560935974121
progress 118859   :  0.007897334649555774 200 25325
time 118859   passed:  0.0029112945000330606  h  expected left:  0.36391181250413257  h
total time 0.06094670295715332
progress 118859   :  0.007936821322803553 201 25325
time 118859   passed:  0.002928224139743381  h  expected left:  0.36420150142035995  h
total time 0.05044150352478027
progress 118859   :  0.007976307996051332 202 25325
time 118859   passed:  0.0029422356685002643  h  expected left:  

...

total time 0.04718899726867676
progress 164377   :  0.9902862783810464 25079 25325
time 164377   passed:  0.40020283506976373  h  expected left:  0.003925434506665147  h
total time 0.045745849609375
progress 164377   :  0.9903257650542941 25080 25325
time 164377   passed:  0.4002155422502108  h  expected left:  0.003909445709951821  h
total time 0.022310256958007812
progress 164377   :  0.990365251727542 25081 25325
time 164377   passed:  0.40022173954381024  h  expected left:  0.003893393846132274  h
total time 0.08542275428771973
progress 164377   :  0.9904047384007897 25082 25325
time 164377   passed:  0.40024546808666794  h  expected left:  0.0038775126079440385  h
total time 0.1039888858795166
progress 164377   :  0.9904442250740375 25083 25325
time 164377   passed:  0.4002743538883011  h  expected left:  0.003861680499161572  h
total time 0.07227206230163574
progress 164377   :  0.9904837117472853 25084 25325
time 164377   passed:  0.40029442946116267  h  expected left:  0.003845

total time 0.02217721939086914
progress 164378   :  0.9923000987166831 25130 25325
time 164378   passed:  0.40126363416512945  h  expected left:  0.0031135413896064717  h
total time 0.026703834533691406
progress 164378   :  0.992339585389931 25131 25325
time 164378   passed:  0.4012710518969444  h  expected left:  0.0030975085177465866  h
total time 0.08437395095825195
progress 164384   :  0.9923790720631787 25132 25325
time 164384   passed:  0.4012944891055439  h  expected left:  0.0030815993473668076  h
total time 0.038481712341308594
progress 164384   :  0.9924185587364265 25133 25325
time 164384   passed:  0.4013051784700831  h  expected left:  0.003065592196477121  h
total time 0.028554439544677734
progress 164384   :  0.9924580454096742 25134 25325
time 164384   passed:  0.40131311025884553  h  expected left:  0.0030495645140019697  h
total time 0.028115034103393555
progress 164384   :  0.992497532082922 25135 25325
time 164384   passed:  0.4013209199905409  h  expected left:  0.

total time 0.05239605903625488
progress 164384   :  0.9942349457058243 25179 25325
time 164384   passed:  0.4023073554701289  h  expected left:  0.002332679662376442  h
total time 0.052597761154174805
progress 164384   :  0.9942744323790721 25180 25325
time 164384   passed:  0.4023219659593384  h  expected left:  0.002316694534137011  h
total time 0.08993649482727051
progress 164384   :  0.9943139190523198 25181 25325
time 164384   passed:  0.40234694831901263  h  expected left:  0.0023007688252695505  h
total time 0.057631492614746094
progress 164384   :  0.9943534057255676 25182 25325
time 164384   passed:  0.4023629570669612  h  expected left:  0.0022847914410743537  h
total time 0.053232669830322266
progress 164384   :  0.9943928923988155 25183 25325
time 164384   passed:  0.40237774391969183  h  expected left:  0.0022688071647314267  h
total time 0.07692766189575195
progress 164384   :  0.9944323790720632 25184 25325
time 164384   passed:  0.4023991127146629  h  expected left:  0.

total time 0.08242917060852051
progress 164398   :  0.9961697926949654 25228 25325
time 164398   passed:  0.403329446183312  h  expected left:  0.0015507137135749045  h
total time 0.08388590812683105
progress 164398   :  0.9962092793682132 25229 25325
time 164398   passed:  0.40335274782445835  h  expected left:  0.0015347548074176774  h
total time 0.08382558822631836
progress 164398   :  0.996248766041461 25230 25325
time 164398   passed:  0.40337603271007677  h  expected left:  0.0015187952561316353  h
total time 0.14650177955627441
progress 164398   :  0.9962882527147088 25231 25325
time 164398   passed:  0.4034167276488424  h  expected left:  0.0015028999841071333  h
total time 0.06097841262817383
progress 164398   :  0.9963277393879566 25232 25325
time 164398   passed:  0.40343366609679465  h  expected left:  0.0014869151883248883  h
total time 0.06288695335388184
progress 164398   :  0.9963672260612043 25233 25325
time 164398   passed:  0.40345113469494853  h  expected left:  0.0

total time 0.06556868553161621
progress 164413   :  0.9981836130306022 25279 25325
time 164413   passed:  0.4045043338669685  h  expected left:  0.0007360442783971737  h
total time 0.05197620391845703
progress 164413   :  0.9982230997038499 25280 25325
time 164413   passed:  0.4045187717013903  h  expected left:  0.0007200405334663408  h
total time 0.07468461990356445
progress 164413   :  0.9982625863770977 25281 25325
time 164413   passed:  0.4045395174291413  h  expected left:  0.0007040478904707782  h
total time 0.05966377258300781
progress 164413   :  0.9983020730503455 25282 25325
time 164413   passed:  0.4045560906993032  h  expected left:  0.0006880477751876771  h
total time 0.0821528434753418
progress 164413   :  0.9983415597235933 25283 25325
time 164413   passed:  0.40457891093360193  h  expected left:  0.0006720579915840563  h
total time 0.04763436317443848
progress 164413   :  0.9983810463968411 25284 25325
time 164413   passed:  0.4045921427011504  h  expected left:  0.000

In [7]:
X = np.asarray(X)
Y = np.asarray(Y)

In [8]:
import pickle as pkl

with open(SESSIONS_PATH + "/dataset_prod_new_model_binary.pkl", "wb") as f:
    pkl.dump([X, Y], f)

In [10]:
Y.shape


(52522,)